In [81]:
import requests
import base64
import json
import pandas as pd
import esoreader
import random
import time
import io
from datetime import datetime

If an error occurs please check if all packages are installed. 

## Check if docker is running

In [82]:
response = requests.get("http://localhost:5000/status")
response.json()

{'success': True}

## Create a new simulation

Create a new sim ID.  

In [83]:
response = requests.post("http://localhost:5000/simulation")
response.json()

'6499dd31e397c16ba054a3eb'

Set the sim ID as a variable. 

In [84]:
simID = response.json()
print("The simulation ID is", simID)

The simulation ID is 6499dd31e397c16ba054a3eb


Returns the information about a simulation with the sim ID from the previous request. 

In [85]:
response = requests.get("http://localhost:5000/simulation", json={"id": simID})
response.json()

{'csv_data': '',
 'date_of_creation': '2023-06-26-20:47',
 'end_day': '',
 'end_month': '',
 'end_year': '',
 'epw_data': '',
 'height': '',
 'idf_data': '',
 'idf_filename': 'SimInput13256379',
 'infiltration_rate': '',
 'length': '',
 'orientation': '',
 'start_day': '',
 'start_month': '',
 'start_year': '',
 'width': '',
 'zone_name': ''}

## Upload files for simulation

Define the path for all simulation files. If the files are in the same directory as the notebook, its only necessary to define the names of the files. Otherwise use the full path to the files. 

In [86]:
idf_file = 'example_room.idf'                    # room model
epw_file = 'DE_Munich_Theresienwiese.epw'        # weather data
csv_file = 'occupancy_1day.csv'                  # occupancy data

Upload files. Files need to be encoded!

In [87]:
#idf file
with open(idf_file, 'rb') as f:
    encoded_object = base64.encodebytes(f.read()).decode('utf-8')

    params = {
     "id":   simID,
     "data": encoded_object
    }
    response = requests.post("http://localhost:5000/idf", json=params)

    response.json() if response.status_code == 200 else print("Failed with status code", response.status_code)

In [88]:
#epw file
with open(epw_file, 'rb') as f:
    encoded_object = base64.encodebytes(f.read()).decode('utf-8')
    
    params = {
     "id":   simID,
     "data": encoded_object
    }
    response = requests.post("http://localhost:5000/weather", json=params)

    response.json() if response.status_code == 200 else print("Failed with status code", response.status_code)

In [89]:
#csv file
with open(csv_file, 'rb') as f:
    encoded_object = base64.encodebytes(f.read()).decode('utf-8')
    
    params = {
     "id":   simID,
     "data": encoded_object
    }
    response = requests.post("http://localhost:5000/occupancy", json=params)

    response.json() if response.status_code == 200 else print("Failed with status code", response.status_code)

To check if all files are uploaded check the contents in the input simulation collection. 

In [90]:
#idf file
response = requests.get("http://localhost:5000/idf", json={"id": simID})
response.json() if response.status_code == 200 else print("Failed with status code", response.status_code)

'  Version,22.2;\n\n  Timestep,6;\n\n  LifeCycleCost:Parameters,\n    Life Cycle Cost Parameters,  !- Name\n    EndOfYear,               !- Discounting Convention\n    ConstantDollar,          !- Inflation Approach\n    0.03,                    !- Real Discount Rate\n    ,                        !- Nominal Discount Rate\n    ,                        !- Inflation\n    ,                        !- Base Date Month\n    2011,                    !- Base Date Year\n    ,                        !- Service Date Month\n    2011,                    !- Service Date Year\n    25,                      !- Length of Study Period in Years\n    ,                        !- Tax rate\n    None;                    !- Depreciation Method\n\n  LifeCycleCost:UsePriceEscalation,\n    U.S. Avg  Commercial-Electricity,  !- LCC Price Escalation Name\n    Electricity,             !- Resource\n    2011,                    !- Escalation Start Year\n    January,                 !- Escalation Start Month\n    0.9838,  

In [91]:
#epw file
response = requests.get("http://localhost:5000/weather", json={"id": simID})
response.json() if response.status_code == 200 else print("Failed with status code", response.status_code)

'LOCATION,Munich-Theresienwiese,BY,DEU,SRC-TMYx,108650,48.16320,11.54290,1.0,520.0\r\nDESIGN CONDITIONS,1,2021 ASHRAE Handbook -- Fundamentals - Chapter 14 Climatic Design Information,,Heating,2,-11.9,-9.2,-15.1,1.1,-10.4,-12.8,1.3,-7.9,10.3,9.2,9.2,7.1,1.8,90,0.476,Cooling,7,8.8,29.5,19.0,27.7,18.1,26.1,17.5,19.7,27.4,18.9,26.1,18.2,24.4,2.6,270,17.2,13.1,21.6,16.4,12.5,21.1,15.8,11.9,20.8,58.6,27.5,55.9,26.3,53.3,24.5,22.7,Extremes,7.8,6.4,5.3,-13.4,33.1,4.3,2.0,-16.5,34.6,-19.0,35.8,-21.4,36.9,-24.5,38.4\r\nTYPICAL/EXTREME PERIODS,6,Summer - Week Nearest Max Temperature For Period,Extreme,8/10,8/16,Summer - Week Nearest Average Temperature For Period,Typical,8/ 3,8/ 9,Winter - Week Nearest Min Temperature For Period,Extreme,12/ 8,12/14,Winter - Week Nearest Average Temperature For Period,Typical,2/17,2/23,Autumn - Week Nearest Average Temperature For Period,Typical,9/29,10/ 5,Spring - Week Nearest Average Temperature For Period,Typical,4/12,4/18\r\nGROUND TEMPERATURES,3,.5,,,,3.97,0

In [92]:
#csv file/occupancy
response = requests.get("http://localhost:5000/occupancy", json={"id": simID})
response.json() if response.status_code == 200 else print("Failed with status code", response.status_code)

'day|time|occupants|win1\n0|00:00:00|0|0\n0|00:01:00|0|0\n0|00:02:00|0|0\n0|00:03:00|0|0\n0|00:04:00|0|0\n0|00:05:00|0|0\n0|00:06:00|0|0\n0|00:07:00|0|0\n0|00:08:00|0|0\n0|00:09:00|0|0\n0|00:10:00|0|0\n0|00:11:00|0|0\n0|00:12:00|0|0\n0|00:13:00|0|0\n0|00:14:00|0|0\n0|00:15:00|0|0\n0|00:16:00|0|0\n0|00:17:00|0|0\n0|00:18:00|0|0\n0|00:19:00|0|0\n0|00:20:00|0|0\n0|00:21:00|0|0\n0|00:22:00|0|0\n0|00:23:00|0|0\n0|00:24:00|0|0\n0|00:25:00|0|0\n0|00:26:00|0|0\n0|00:27:00|0|0\n0|00:28:00|0|0\n0|00:29:00|0|0\n0|00:30:00|0|0\n0|00:31:00|0|0\n0|00:32:00|0|0\n0|00:33:00|0|0\n0|00:34:00|0|0\n0|00:35:00|0|0\n0|00:36:00|0|0\n0|00:37:00|0|0\n0|00:38:00|0|0\n0|00:39:00|0|0\n0|00:40:00|0|0\n0|00:41:00|0|0\n0|00:42:00|0|0\n0|00:43:00|0|0\n0|00:44:00|0|0\n0|00:45:00|0|0\n0|00:46:00|0|0\n0|00:47:00|0|0\n0|00:48:00|0|0\n0|00:49:00|0|0\n0|00:50:00|0|0\n0|00:51:00|0|0\n0|00:52:00|0|0\n0|00:53:00|0|0\n0|00:54:00|0|0\n0|00:55:00|0|0\n0|00:56:00|0|0\n0|00:57:00|0|0\n0|00:58:00|0|0\n0|00:59:00|0|0\n0|01:00:00|0|0

## Set parameters/metadata for simulation

Define the parameters. Set the timeframe and room parameters for the simulation. The zone name can be found in the idf file. If the zone name does not match the zone name in the idf file an energy plus error occurs. 

In [93]:
params = {
 "id": simID,
 "height": 3,
 "length": 5,
 "width": 4,
 "orientation":0,
 "start_day": 1,
 "start_month": 6,
 "start_year": 2022,
 "end_day": 1,
 "end_month": 6,
 "end_year": 2022,
 "infiltration_rate": 0.0019, 
 "zone_name": "RL_Office_27214585"
}

## Start a simulation

In [94]:
response = requests.post("http://localhost:5000/simulation/control", json=params)
response.json()

{'success': True}

Check the status of the simulation: 

In [96]:
response = requests.get("http://localhost:5000/simulation/control", json={"id": simID})
response.json()

{'status': 'done'}

## Results

Check the results for the simulation. This will fail until the simulation has completed sucessfully.  

In [97]:
response = requests.get("http://localhost:5000/result", json={"id": simID})
response.json() if response.status_code == 200 else print("Failed with status code", response.status_code)

{'_id': '6499dd84e397c16ba054a3fe',
 'date_of_creation': '2023-06-26-20:48',
 'eso_data': '...\n',
 'filename': 'SimOutput36754009',
 'idf_data': '...\nYXI7ICAgICAgICAgIS0gT3B0aW9uIFR5cGU=\n',
 'sim_id': '6499dd31e397c16ba054a3eb',
 'status': 'done'}

To see the results in a table this endpoint can be used.

In [98]:
response = requests.get("http://localhost:5000/result/csv", json={"id": simID})
response 

<Response [200]>

To view the csv data in a table use the following:

In [99]:
csv_data = io.BytesIO(response.content)
df = pd.read_csv(csv_data)
df.head()

date  zone_air_temperature  zone_co2_concentration   
0  2022-06-01 00:00             22.444013             1108.273413  \
1  2022-06-01 00:01             22.440291             1107.175398   
2  2022-06-01 00:02             22.436333             1106.078853   
3  2022-06-01 00:03             22.432135             1104.983774   
4  2022-06-01 00:04             22.427712             1103.890163   

   zone_rel_humidity  outdoor_air_pressure  outdoor_air_drybulb  occupancy   
0          63.958120          95590.316667                13.03          0  \
1          63.947149          95588.633333                12.96          0   
2          63.936722          95586.950000                12.89          0   
3          63.926852          95585.266667                12.82          0   
4          63.917489          95583.583333                12.75          0   

   window  
0       0  
1       0  
2       0  
3       0  
4       0

## View simulation inputs of a simulation 

Returns the metadata of a simulation. This will only return the inforamtion after the simulation was run and the data was saved in the databse. 

In [100]:
response = requests.get("http://localhost:5000/metadata", json={"id": simID})
response.json()

{'end_day': 1,
 'end_month': 6,
 'end_year': 2022,
 'height': 3.0,
 'infiltration_rate': 0.0019,
 'length': 5.0,
 'orientation': 0,
 'start_day': 1,
 'start_month': 6,
 'start_year': 2022,
 'width': 4.0,
 'zone_name': 'RL_Office_27214585'}

## Overview on all simulations in database

Overview on all initiated simulations in the database. The response will return the simulations from the input_simulation collection. 

In [101]:
response = requests.get("http://localhost:5000/simulation/overview")
response.json()

[{'_id': '643072a6b167660e37cb196f',
  'date_of_creation': '2023-04-07-21:44',
  'idf_filename': 'SimInput38925173'},
 {'_id': '6430832b8937612757b4ffbd',
  'date_of_creation': '2023-04-07-22:55',
  'idf_filename': 'SimInput07572191'},
 {'_id': '64359a098937612757b4ffcc',
  'date_of_creation': '2023-04-11-19:34',
  'idf_filename': 'SimInput01535043'},
 {'_id': '6436b4388937612757b4ffce',
  'date_of_creation': '2023-04-12-15:38',
  'idf_filename': 'SimInput00868007'},
 {'_id': '6436b98b21d66184742714d2',
  'date_of_creation': '2023-04-12-16:00',
  'idf_filename': 'SimInput43181951'},
 {'_id': '6436be870376669499171460',
  'date_of_creation': '2023-04-12-16:21',
  'idf_filename': 'SimInput59766317'},
 {'_id': '6437ce8af1d2ce3f037ea169',
  'date_of_creation': '2023-04-13-11:42',
  'idf_filename': 'SimInput34321252'},
 {'_id': '6437d0afe2e46162bbb77127',
  'date_of_creation': '2023-04-13-11:51',
  'idf_filename': 'SimInput43405605'},
 {'_id': '6437e2952e0f9ba3fd2aec1b',
  'date_of_creation

## Overview on all results in database

Overview on all performed simulations. The response will return all results from the simulation_result collection. 

In [102]:
response = requests.get("http://localhost:5000/result/overview")
response.json()

[{'_id': '6499dd84e397c16ba054a3fe',
  'date_of_creation': '2023-06-26-20:48',
  'filename': 'SimOutput36754009',
  'input_simulation_id': '6499dd31e397c16ba054a3eb',
  'status': 'done'},
 {'_id': '6499d177475b75d3e877b71e',
  'date_of_creation': '2023-06-26-19:57',
  'filename': 'SimOutput11260636',
  'input_simulation_id': '6499c476475b75d3e877b641',
  'status': 'done'},
 {'_id': '6499d146475b75d3e877b70f',
  'date_of_creation': '2023-06-26-19:56',
  'filename': 'SimOutput22912966',
  'input_simulation_id': '6499c476475b75d3e877b63d',
  'status': 'done'},
 {'_id': '6499d116475b75d3e877b700',
  'date_of_creation': '2023-06-26-19:55',
  'filename': 'SimOutput34713341',
  'input_simulation_id': '6499c476475b75d3e877b639',
  'status': 'done'},
 {'_id': '6499d0e1475b75d3e877b6f1',
  'date_of_creation': '2023-06-26-19:54',
  'filename': 'SimOutput41492634',
  'input_simulation_id': '6499c476475b75d3e877b635',
  'status': 'done'},
 {'_id': '6499d0bd475b75d3e877b6e2',
  'date_of_creation': '

## Delete a simulation

Example how to delete a simulation from the input_simulation collection in the database (The results will not be deleted). 

In [103]:
simID = "6440652aceed9cc1acc4251a"
response = requests.delete("http://localhost:5000/simulation", json={"id": simID})
response.json()

{'success': True}

## Delete result entry of a simulation

In [104]:
simID = "6440652aceed9cc1acc4251a"
response = requests.delete("http://localhost:5000/result", json={"id": simID})
response.json()

{'success': True}

## Simulation with only an idf and epw file

It is possible to run a simulation and only upload an idf and epw file. But different endpoints need to be used. Here is an example: 

First initiate a new simulation. 

In [105]:
response = requests.post("http://localhost:5000/simulation")
response.json()

'6499df05e397c16ba054a407'

And set the sim ID

In [106]:
simID = response.json()
print("The simulation ID is", simID)

The simulation ID is 6499df05e397c16ba054a407


Upload the idf and epw file: 

In [107]:
idf_file = 'example_room.idf'                    # room model
epw_file = 'DE_Munich_Theresienwiese.epw'        # weather data

In [108]:
#idf file
with open(idf_file, 'rb') as f:
    encoded_object = base64.encodebytes(f.read()).decode('utf-8')

    params = {
     "id":   simID,
     "data": encoded_object
    }
    response = requests.post("http://localhost:5000/idf", json=params)

    response.json() if response.status_code == 200 else print("Failed with status code", response.status_code)

In [109]:
#epw file
with open(epw_file, 'rb') as f:
    encoded_object = base64.encodebytes(f.read()).decode('utf-8')
    
    params = {
     "id":   simID,
     "data": encoded_object
    }
    response = requests.post("http://localhost:5000/weather", json=params)

    response.json() if response.status_code == 200 else print("Failed with status code", response.status_code)

Start the simulation with the correct endpoint: 

In [110]:
response = requests.post("http://localhost:5000/simulation/control/onlyidf", json={"id": simID})
response.json()

{'success': True}

Check the status of the simulation.

In [111]:
response = requests.get("http://localhost:5000/simulation/control", json={"id": simID})
response.json()

{'status': 'done'}

Check if results are in database. This will fail until the simulation has completed successfully

In [113]:
response = requests.get("http://localhost:5000/result", json={"id": simID})
response if response.status_code == 200 else print("Failed with status code", response.status_code)

<Response [200]>

Return the status of an simulation which was run with only an idf and epw file (same response like simulation/control)

In [114]:
response = requests.get("http://localhost:5000/simulation/control/onlyidf", json={"id": simID})
response.json()

{'status': 'done'}

## Reopen an old simulation

It is possible to reopen an old simulation. This means all the input data which was used in the simulation will be available again and it is possible to edit the parameter and start a new simulation. This will not change the data of the old simulation ID. It will always initiate a new simulation. 

To reopen an old simulation, the sim ID from the database is needed. The GET request will return all input data. This is necessary to copy the parameters for the simulation. 

In [115]:
simID = "64998548b04d0bcba8f22b4d"
response = requests.get("http://localhost:5000/reopensim", json={"id": simID})
response.json()

[{'end_day': 1,
  'end_month': 6,
  'end_year': 2022,
  'height': 3.0,
  'infiltration_rate': 0.0019,
  'length': 5.0,
  'orientation': 0,
  'start_day': 1,
  'start_month': 6,
  'start_year': 2022,
  'width': 4.0,
  'zone_name': 'RL_Office_27214585'},
 '  Version,22.2;\n\n  Timestep,6;\n\n  LifeCycleCost:Parameters,\n    Life Cycle Cost Parameters,  !- Name\n    EndOfYear,               !- Discounting Convention\n    ConstantDollar,          !- Inflation Approach\n    0.03,                    !- Real Discount Rate\n    ,                        !- Nominal Discount Rate\n    ,                        !- Inflation\n    ,                        !- Base Date Month\n    2011,                    !- Base Date Year\n    ,                        !- Service Date Month\n    2011,                    !- Service Date Year\n    25,                      !- Length of Study Period in Years\n    ,                        !- Tax rate\n    None;                    !- Depreciation Method\n\n  LifeCycleCost:Us

With the post request a new simulation is created in the database. The parameter here is the sim ID from the old simulation. This request retrieves all inforamtion from the old simulation and inserts it in the database with a new sim ID. It will return the sim ID from the new simulation. With this sim ID it is possible to edit the data or upload new files. The csv, idf and epw file were all automatically uploaded in the dadabase with the new sim ID. To change the data use the requests from above (upload files, set metadata, etc.)

In [116]:
response = requests.post("http://localhost:5000/reopensim", json={"id": simID})
response.json()

'6499e020e397c16ba054a41d'

Copy now the sim ID and set the sim ID in the parameters. Copy the parameters from above (GET request)(but only parameter, not the information about the files) and now its possible to run a new simulation. It is not required to upload the files here because the csv, idf and epw files from the old simulation were uploaded to the database. But it it necessary to insert here the paramerters again, because the POST request from simulation/control expects the parameters in the request body. 

In [117]:
simID = "6499e020e397c16ba054a41d"
params = {
 "id": simID,
 'end_day': 1,
 'end_month': 6,
 'end_year': 2022,
 'height': 3.0,
 'infiltration_rate': 0.0019,
 'length': 5.0,
 'orientation': 0,
 'start_day': 1,
 'start_month': 6,
 'start_year': 2022,
 'width': 4.0,
 'zone_name': 'RL_Office_27214585'}

response = requests.post("http://localhost:5000/simulation/control", json=params)
response.json()

{'success': True}

Check status of simulation

In [119]:
response = requests.get("http://localhost:5000/simulation/control", json={"id": simID})
response.json()

{'status': 'done'}

## Simulation Series

A simulation series will run mulitple simulation with the same idf, epw  and csv file but the room parameters can be adjusted. Here is an example on how to create a series. 

Information: a series will take some time depending on the variations! Upload of files, create a simulation etc. will all take more time than a single simulation!

In [69]:
params = {
    "height": 7,
    "height_max": 8,
    "height_iter": 1,
    "length": 11,
    "length_max": 12,
    "length_iter": 1,
    "width": 4,
    "width_max": 6,
    "width_iter": 1,
    "orientation": 0,
    "orientation_max": 0,
    "orientation_iter": 0,
    "start_day": 17,
    "start_month": 5,
    "start_year": 2023,
    "end_day": 17,
    "end_month": 5,
    "end_year": 2023,
    "infiltration_rate": 0.0019,
    "infiltration_rate_max": 0.0019,
    "infiltration_rate_iter": 0
}
response = requests.post("http://localhost:5000/series/create", json=params)
response.json()

'6499c476475b75d3e877b613'

Set sim ID

In [70]:
sim_ser_id = response.json()
print(sim_ser_id)

6499c476475b75d3e877b613


Height: 7 - 8 Length: 11 - 12 Width: 4 - 5 - 6 => 12 Variationen (2 * 2 * 3)
This example will run 12 simulation. When the simulation is startet it will take a while!It depends on the number of simulations!

Add files to simulation 

In [71]:
idf_file = 'example_room.idf'                    # room model
epw_file = 'DE_Munich_Theresienwiese.epw'        # weather data
csv_file = 'occupancy_1day.csv'                  # occupancy data

In [72]:
with open(csv_file, 'rb') as f:
    encoded_object = base64.encodebytes(f.read()).decode('utf-8')

    params = {
        "id": sim_ser_id,
        "data": encoded_object
    }
    response = requests.post("http://localhost:5000/series/occupancy", json=params)

response.json() if response.status_code == 200 else print("Failed with status code", response.status_code)

{'success': True}

In [73]:
with open(idf_file, 'rb') as f:
    encoded_object = base64.encodebytes(f.read()).decode('utf-8')

    params = {
        "id": sim_ser_id,
        "data": encoded_object
    }
    response = requests.post("http://localhost:5000/series/idf", json=params)

response.json() if response.status_code == 200 else print("Failed with status code", response.status_code)

{'success': True}

In [74]:
with open(epw_file, 'rb') as f:
    encoded_object = base64.encodebytes(f.read()).decode('utf-8')

    params = {
        "id": sim_ser_id,
        "data": encoded_object
    }
    response = requests.post("http://localhost:5000/series/weather", json=params)

response.json() if response.status_code == 200 else print("Failed with status code", response.status_code)

{'success': True}

Start a simulation series

In [75]:
response = requests.post("http://localhost:5000/series/run", json={"id": sim_ser_id})
response.json()

{'success': True}

Return status of simulation

In [77]:
response = requests.get("http://localhost:5000/series/run", json={"id": sim_ser_id})
response.json()

{'status': 'Done'}

In [ ]:
View results of series simulation run

In [80]:
response = requests.get("http://localhost:5000/series/results", json={"id": sim_ser_id})
response.json()

['6499c476475b75d3e877b615',
 '6499c476475b75d3e877b619',
 '6499c476475b75d3e877b61d',
 '6499c476475b75d3e877b621',
 '6499c476475b75d3e877b625',
 '6499c476475b75d3e877b629',
 '6499c476475b75d3e877b62d',
 '6499c476475b75d3e877b631',
 '6499c476475b75d3e877b635',
 '6499c476475b75d3e877b639',
 '6499c476475b75d3e877b63d',
 '6499c476475b75d3e877b641']